In [1]:
import geopandas as gpd
import pandas as pd
import numpy as np
import folium
from matplotlib import pyplot as plt
from geopy.geocoders import Nominatim
from folium import Marker, Choropleth
import warnings 
warnings.filterwarnings('ignore')

In [2]:
geolocator = Nominatim(user_agent="Preço Commodities")
location = geolocator.geocode("Kyiv")

In [3]:
point = location.point
print("Latitude:", point.latitude)
print("Longitude:", point.longitude)

Latitude: 50.4500336
Longitude: 30.5241361


In [4]:
file_path = "../Dados/Ukraine_commodities_prices.csv"

attrs = ['market', 'price', 'date', 'commodity', 'priceflag']

regioes = pd.read_csv(file_path,  dtype='unicode')
regioes = regioes[1:][attrs]

rice_prices = regioes[(regioes['commodity'] == 'Rice') & (regioes['priceflag'] == 'actual')]

rice_prices['year'] = rice_prices['date'].str[0:4]
rice_prices['price'] = pd.to_numeric(rice_prices['price'])

rice_pre2022 = rice_prices[rice_prices['year'] < '2022']
rice_post2022 = rice_prices[rice_prices['year'] >= '2022']

rice_pre2022 = rice_pre2022.groupby('market')[['price']].max().reset_index()
rice_post2022 = rice_post2022.groupby('market')[['price']].max().reset_index()

display(rice_pre2022)
display(rice_post2022)

market  price
0           Cherkasy  26.67
1          Chernihiv  25.59
2         Chernivtsi  28.23
3             Crimea   7.76
4     Dnipropetrovsk  27.99
5            Donetsk  33.90
6      Iv.-Frankivsk  28.20
7            Kharkiv  27.12
8            Kherson  29.14
9       Khmelnytskiy  28.13
10        Kirovohrad  25.12
11              Kyiv  31.49
12         Kyiv city  29.75
13           Luhansk  30.09
14              Lviv  29.37
15         Mykolayiv  25.67
16  National Average  24.01
17             Odesa  29.11
18           Poltava  27.06
19             Rivne  26.24
20              Sumy  26.09
21          Ternopyl  27.75
22         Vinnytsya  26.17
23             Volyn  29.14
24       Zakarpattya  28.52
25      Zaporizhzhya  30.11
26          Zhytomyr  29.25
27     m. Sevastopol   9.42

market  price
0         Cherkasy  57.33
1        Chernihiv  58.01
2       Chernivtsi  63.75
3   Dnipropetrovsk  61.18
4          Donetsk  33.78
5    Iv.-Frankivsk  59.06
6          Kharkiv  59.93
7          Kherson  57.82
8     Khmelnytskiy  58.36
9             Kyiv  65.67
10       Kyiv city  58.45
11            Lviv  62.30
12       Mykolayiv  53.54
13           Odesa  59.73
14         Poltava  57.33
15           Rivne  60.32
16            Sumy  60.41
17        Ternopyl  63.96
18       Vinnytsya  58.20
19           Volyn  59.60
20     Zakarpattya  62.41
21    Zaporizhzhya  62.31
22        Zhytomyr  61.66

In [5]:
geo_regioes = gpd.read_file("../Dados/ukraine_regions.geojson")

geo_reg = geo_regioes[["region_en", "geometry"]]

display(geo_reg)

geo_reg.describe()
geo_reg["market"] = geo_reg["region_en"].map(lambda x: x.replace(" Oblast", ""))

#geo_reg = geo_reg.rename(columns = {"region_en": "market"})

#geo_reg = geo_reg.set_index("market")

display(geo_reg)

region_en  \
0                 Cherkasy Oblast   
1                Chernihiv Oblast   
2               Chernivtsi Oblast   
3   Autonomous Republic of Crimea   
4           Dnipropetrovsk Oblast   
5                  Donetsk Oblast   
6          Ivano-Frankivsk Oblast   
7                  Kharkiv Oblast   
8                  Kherson Oblast   
9             Khmelnytskyi Oblast   
10                           Kyiv   
11                    Kyiv Oblast   
12              Kirovohrad Oblast   
13                    Lviv Oblast   
14                 Luhansk Oblast   
15                Mykolaiv Oblast   
16                   Odesa Oblast   
17                 Poltava Oblast   
18                   Rivne Oblast   
19                     Sevastopol   
20                    Sumy Oblast   
21                Ternopil Oblast   
22             Zakarpattia Oblast   
23               Vinnytsia Oblast   
24                   Volyn Oblast   
25            Zaporizhzhia Oblast   
26                Zhytomyr Oblast   

                                             geometry  
0   POLYGON ((32.15047 50.19769, 32.15050 50.19181...  
1   POLYGON ((33.19667 52.37500, 33.20612 52.36700...  
2   POLYGON ((25.62595 48.67673, 25.64460 48.67159...  
3   MULTIPOLYGON (((33.79458 44.39153, 33.79291 44...  
4   POLYGON ((34.92995 49.15574, 34.92076 49.14992...  
5   MULTIPOLYGON (((37.67542 47.08208, 37.67542 47...  
6   POLYGON ((24.48923 49.53322, 24.49895 49.52786...  
7   POLYGON ((36.07391 50.46371, 36.08271 50.45771...  
8   MULTIPOLYGON (((34.05688 46.01227, 34.05639 46...  
9   POLYGON ((27.13142 50.56980, 27.14136 50.56425...  
10  POLYGON ((30.46630 50.58701, 30.46658 50.58113...  
11  POLYGON ((29.73023 51.52906, 29.73049 51.52345...  
12  POLYGON ((32.95085 49.20770, 32.96899 49.20749...  
13  POLYGON ((24.21482 50.62987, 24.22468 50.62470...  
14  POLYGON ((38.34765 50.08024, 38.34533 50.06713...  
15  MULTIPOLYGON (((31.41125 46.60264, 31.41125 46...  
16  MULTIPOLYGON (((30.20708 45.25764, 30.20708 45...  
17  POLYGON ((34.03342 50.50913, 34.05145 50.49718...  
18  POLYGON ((25.82499 51.96153, 25.84438 51.95672...  
19  POLYGON ((33.56181 44.84153, 33.56181 44.84125...  
20  POLYGON ((33.79665 52.36000, 33.81583 52.34790...  
21  POLYGON ((26.21350 50.25444, 26.21611 50.23071...  
22  POLYGON ((22.60218 49.09510, 22.60193 49.09060...  
23  POLYGON ((28.97885 49.83524, 28.97919 49.82933...  
24  POLYGON ((25.30289 51.97861, 25.32052 51.97417...  
25  MULTIPOLYGON (((35.05986 46.15125, 35.05986 46...  
26  POLYGON ((28.25902 51.63647, 28.25941 51.63033...

region_en  \
0                 Cherkasy Oblast   
1                Chernihiv Oblast   
2               Chernivtsi Oblast   
3   Autonomous Republic of Crimea   
4           Dnipropetrovsk Oblast   
5                  Donetsk Oblast   
6          Ivano-Frankivsk Oblast   
7                  Kharkiv Oblast   
8                  Kherson Oblast   
9             Khmelnytskyi Oblast   
10                           Kyiv   
11                    Kyiv Oblast   
12              Kirovohrad Oblast   
13                    Lviv Oblast   
14                 Luhansk Oblast   
15                Mykolaiv Oblast   
16                   Odesa Oblast   
17                 Poltava Oblast   
18                   Rivne Oblast   
19                     Sevastopol   
20                    Sumy Oblast   
21                Ternopil Oblast   
22             Zakarpattia Oblast   
23               Vinnytsia Oblast   
24                   Volyn Oblast   
25            Zaporizhzhia Oblast   
26                Zhytomyr Oblast   

                                             geometry  \
0   POLYGON ((32.15047 50.19769, 32.15050 50.19181...   
1   POLYGON ((33.19667 52.37500, 33.20612 52.36700...   
2   POLYGON ((25.62595 48.67673, 25.64460 48.67159...   
3   MULTIPOLYGON (((33.79458 44.39153, 33.79291 44...   
4   POLYGON ((34.92995 49.15574, 34.92076 49.14992...   
5   MULTIPOLYGON (((37.67542 47.08208, 37.67542 47...   
6   POLYGON ((24.48923 49.53322, 24.49895 49.52786...   
7   POLYGON ((36.07391 50.46371, 36.08271 50.45771...   
8   MULTIPOLYGON (((34.05688 46.01227, 34.05639 46...   
9   POLYGON ((27.13142 50.56980, 27.14136 50.56425...   
10  POLYGON ((30.46630 50.58701, 30.46658 50.58113...   
11  POLYGON ((29.73023 51.52906, 29.73049 51.52345...   
12  POLYGON ((32.95085 49.20770, 32.96899 49.20749...   
13  POLYGON ((24.21482 50.62987, 24.22468 50.62470...   
14  POLYGON ((38.34765 50.08024, 38.34533 50.06713...   
15  MULTIPOLYGON (((31.41125 46.60264, 31.41125 46...   
16  MULTIPOLYGON (((30.20708 45.25764, 30.20708 45...   
17  POLYGON ((34.03342 50.50913, 34.05145 50.49718...   
18  POLYGON ((25.82499 51.96153, 25.84438 51.95672...   
19  POLYGON ((33.56181 44.84153, 33.56181 44.84125...   
20  POLYGON ((33.79665 52.36000, 33.81583 52.34790...   
21  POLYGON ((26.21350 50.25444, 26.21611 50.23071...   
22  POLYGON ((22.60218 49.09510, 22.60193 49.09060...   
23  POLYGON ((28.97885 49.83524, 28.97919 49.82933...   
24  POLYGON ((25.30289 51.97861, 25.32052 51.97417...   
25  MULTIPOLYGON (((35.05986 46.15125, 35.05986 46...   
26  POLYGON ((28.25902 51.63647, 28.25941 51.63033...   

                           market  
0                        Cherkasy  
1                       Chernihiv  
2                      Chernivtsi  
3   Autonomous Republic of Crimea  
4                  Dnipropetrovsk  
5                         Donetsk  
6                 Ivano-Frankivsk  
7                         Kharkiv  
8                         Kherson  
9                    Khmelnytskyi  
10                           Kyiv  
11                           Kyiv  
12                     Kirovohrad  
13                           Lviv  
14                        Luhansk  
15                       Mykolaiv  
16                          Odesa  
17                        Poltava  
18                          Rivne  
19                     Sevastopol  
20                           Sumy  
21                       Ternopil  
22                    Zakarpattia  
23                      Vinnytsia  
24                          Volyn  
25                   Zaporizhzhia  
26                       Zhytomyr

In [6]:
markets = geo_reg.index
marks = rice_pre2022['market'].tolist()

print(list(markets))
print(marks)

[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26]
['Cherkasy', 'Chernihiv', 'Chernivtsi', 'Crimea', 'Dnipropetrovsk', 'Donetsk', 'Iv.-Frankivsk', 'Kharkiv', 'Kherson', 'Khmelnytskiy', 'Kirovohrad', 'Kyiv', 'Kyiv city', 'Luhansk', 'Lviv', 'Mykolayiv', 'National Average', 'Odesa', 'Poltava', 'Rivne', 'Sumy', 'Ternopyl', 'Vinnytsya', 'Volyn', 'Zakarpattya', 'Zaporizhzhya', 'Zhytomyr', 'm. Sevastopol']


In [26]:
food_price_map = folium.Map(location = [48, 31], tiles = 'cartodbpositron', zoom_start = 6)

final_food_prices = geo_reg.merge(rice_pre2022, on = 'market')

Choropleth(
    geo_data = final_food_prices,
    data = final_food_prices,
    columns = ['region_en', 'price'],
    key_on = "feature.properties.region_en", 
    fill_color = 'YlGnBu',
    bins = [x for x in range(20, 71, 5)],
    legend_name = "Preço máximo do arroz em regiões da Ucrânia no pré Guerra"
).add_to(food_price_map)

food_price_map

In [9]:
display(final_food_prices)

region_en                                           geometry  \
0         Cherkasy Oblast  POLYGON ((32.15047 50.19769, 32.15050 50.19181...   
1        Chernihiv Oblast  POLYGON ((33.19667 52.37500, 33.20612 52.36700...   
2       Chernivtsi Oblast  POLYGON ((25.62595 48.67673, 25.64460 48.67159...   
3   Dnipropetrovsk Oblast  POLYGON ((34.92995 49.15574, 34.92076 49.14992...   
4          Donetsk Oblast  MULTIPOLYGON (((37.67542 47.08208, 37.67542 47...   
5          Kharkiv Oblast  POLYGON ((36.07391 50.46371, 36.08271 50.45771...   
6          Kherson Oblast  MULTIPOLYGON (((34.05688 46.01227, 34.05639 46...   
7                    Kyiv  POLYGON ((30.46630 50.58701, 30.46658 50.58113...   
8             Kyiv Oblast  POLYGON ((29.73023 51.52906, 29.73049 51.52345...   
9       Kirovohrad Oblast  POLYGON ((32.95085 49.20770, 32.96899 49.20749...   
10            Lviv Oblast  POLYGON ((24.21482 50.62987, 24.22468 50.62470...   
11         Luhansk Oblast  POLYGON ((38.34765 50.08024, 38.34533 50.06713...   
12           Odesa Oblast  MULTIPOLYGON (((30.20708 45.25764, 30.20708 45...   
13         Poltava Oblast  POLYGON ((34.03342 50.50913, 34.05145 50.49718...   
14           Rivne Oblast  POLYGON ((25.82499 51.96153, 25.84438 51.95672...   
15            Sumy Oblast  POLYGON ((33.79665 52.36000, 33.81583 52.34790...   
16           Volyn Oblast  POLYGON ((25.30289 51.97861, 25.32052 51.97417...   
17        Zhytomyr Oblast  POLYGON ((28.25902 51.63647, 28.25941 51.63033...   

            market  price  
0         Cherkasy  26.67  
1        Chernihiv  25.59  
2       Chernivtsi  28.23  
3   Dnipropetrovsk  27.99  
4          Donetsk  33.90  
5          Kharkiv  27.12  
6          Kherson  29.14  
7             Kyiv  31.49  
8             Kyiv  31.49  
9       Kirovohrad  25.12  
10            Lviv  29.37  
11         Luhansk  30.09  
12           Odesa  29.11  
13         Poltava  27.06  
14           Rivne  26.24  
15            Sumy  26.09  
16           Volyn  29.14  
17        Zhytomyr  29.25

In [25]:
food_price_map = folium.Map(location = [48, 31], tiles = 'cartodbpositron', zoom_start = 6)

final_food_prices = geo_reg.merge(rice_post2022, on = 'market')

Choropleth(
    geo_data = final_food_prices,
    data = final_food_prices,
    columns = ['region_en', 'price'],
    key_on = "feature.properties.region_en", 
    fill_color = 'YlGnBu',
    bins = [x for x in range(20, 71, 5)],
    legend_name = "Preço máximo do arroz em regiões da Ucrânia no pós Guerra"
).add_to(food_price_map)

food_price_map

In [11]:
display(final_food_prices)

region_en                                           geometry  \
0         Cherkasy Oblast  POLYGON ((32.15047 50.19769, 32.15050 50.19181...   
1        Chernihiv Oblast  POLYGON ((33.19667 52.37500, 33.20612 52.36700...   
2       Chernivtsi Oblast  POLYGON ((25.62595 48.67673, 25.64460 48.67159...   
3   Dnipropetrovsk Oblast  POLYGON ((34.92995 49.15574, 34.92076 49.14992...   
4          Donetsk Oblast  MULTIPOLYGON (((37.67542 47.08208, 37.67542 47...   
5          Kharkiv Oblast  POLYGON ((36.07391 50.46371, 36.08271 50.45771...   
6          Kherson Oblast  MULTIPOLYGON (((34.05688 46.01227, 34.05639 46...   
7                    Kyiv  POLYGON ((30.46630 50.58701, 30.46658 50.58113...   
8             Kyiv Oblast  POLYGON ((29.73023 51.52906, 29.73049 51.52345...   
9             Lviv Oblast  POLYGON ((24.21482 50.62987, 24.22468 50.62470...   
10           Odesa Oblast  MULTIPOLYGON (((30.20708 45.25764, 30.20708 45...   
11         Poltava Oblast  POLYGON ((34.03342 50.50913, 34.05145 50.49718...   
12           Rivne Oblast  POLYGON ((25.82499 51.96153, 25.84438 51.95672...   
13            Sumy Oblast  POLYGON ((33.79665 52.36000, 33.81583 52.34790...   
14           Volyn Oblast  POLYGON ((25.30289 51.97861, 25.32052 51.97417...   
15        Zhytomyr Oblast  POLYGON ((28.25902 51.63647, 28.25941 51.63033...   

            market  price  
0         Cherkasy  57.33  
1        Chernihiv  58.01  
2       Chernivtsi  63.75  
3   Dnipropetrovsk  61.18  
4          Donetsk  33.78  
5          Kharkiv  59.93  
6          Kherson  57.82  
7             Kyiv  65.67  
8             Kyiv  65.67  
9             Lviv  62.30  
10           Odesa  59.73  
11         Poltava  57.33  
12           Rivne  60.32  
13            Sumy  60.41  
14           Volyn  59.60  
15        Zhytomyr  61.66

In [12]:
print(help(Choropleth))

Help on class Choropleth in module folium.features:

class Choropleth(folium.map.FeatureGroup)
 |  Choropleth(geo_data, data=None, columns=None, key_on=None, bins=6, fill_color=None, nan_fill_color='black', fill_opacity=0.6, nan_fill_opacity=None, line_color='black', line_weight=1, line_opacity=1, name=None, legend_name='', overlay=True, control=True, show=True, topojson=None, smooth_factor=None, highlight=None, use_jenks=False, **kwargs)
 |  
 |  Apply a GeoJSON overlay to the map.
 |  
 |  Plot a GeoJSON overlay on the base map. There is no requirement
 |  to bind data (passing just a GeoJSON plots a single-color overlay),
 |  but there is a data binding option to map your columnar data to
 |  different feature objects with a color scale.
 |  
 |  If data is passed as a Pandas DataFrame, the "columns" and "key-on"
 |  keywords must be included, the first to indicate which DataFrame
 |  columns to use, the second to indicate the layer in the GeoJSON
 |  on which to key the data. The '

In [13]:
print(help(final_food_prices))

Help on GeoDataFrame in module geopandas.geodataframe object:

class GeoDataFrame(geopandas.base.GeoPandasBase, pandas.core.frame.DataFrame)
 |  GeoDataFrame(data=None, *args, geometry=None, crs=None, **kwargs)
 |  
 |  A GeoDataFrame object is a pandas.DataFrame that has a column
 |  with geometry. In addition to the standard DataFrame constructor arguments,
 |  GeoDataFrame also accepts the following keyword arguments:
 |  
 |  Parameters
 |  ----------
 |  crs : value (optional)
 |      Coordinate Reference System of the geometry objects. Can be anything accepted by
 |      :meth:`pyproj.CRS.from_user_input() <pyproj.crs.CRS.from_user_input>`,
 |      such as an authority string (eg "EPSG:4326") or a WKT string.
 |  geometry : str or array (optional)
 |      If str, column to use as geometry. If array, will be set as 'geometry'
 |      column on GeoDataFrame.
 |  
 |  Examples
 |  --------
 |  Constructing GeoDataFrame from a dictionary.
 |  
 |  >>> from shapely.geometry import Poi


None
